In [1]:
!pip install nglview -user

/usr/bin/bash: line 1: pip: command not found


In [2]:
import nglview as nv
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json

In [3]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [4]:
#   Ключевые слова: amoxicillin
#   Где они должны быть: title (в parameters далее attribute)

keyword_clause = {
    "type": "terminal",
    "service": "text", # Сервис поиска где угодно, в любом текстовом 
                            # поле записи. Не гарантирует точного соответствия
    "parameters": {
        "value": "amoxicillin",
        "attribute": "struct.title",
        "operator": "contains_words"
        
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [5]:
# Какое разрешение: не хуже 2.8 ангстрем

resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.8,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [6]:
# Сколько лигандов должно быть в записи: не меньше 1 (то есть больше 0)

has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [7]:
# Дата публикации записи: с 2000-01-01 по  2005-01-01

date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2000-01-01", # год-месяц-день
            "to": "2005-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [8]:
# Префикс адреса, по которому нужно отослать запрос. 
# Сам запрос должен быть сформирован в виде строки и подан аргументу data

rcsb = 'https://search.rcsb.org/rcsbsearch/v2/query'

json_query = json.dumps(my_query) # Функция dumps буквально значит "dump string", 
                                  # то есть превращает словарь в строку 
                                  # с правильным форматированием

search = requests.post(f'{rcsb}', data=json_query) # Отсылаем запрос

In [9]:
search # если выдаст <Response [200]> значит все в порядке

<Response [200]>

In [10]:
search_result = search.json() # Распаковываем ответ сервера в словарь
search_result

{'query_id': 'f27bb8a0-8af3-4b01-97f1-07f3acfcf082',
 'result_type': 'entry',
 'total_count': 1,
 'result_set': [{'identifier': '1LL9', 'score': 1.0}]}

In [11]:
best_hit = search_result["result_set"][0] # Лучшая находка
best_hit

{'identifier': '1LL9', 'score': 1.0}

In [12]:
# я работаю с 1LL9

In [13]:
#Задание 2

In [14]:
# Амоксицилин это антибиотик. Результат 1LL9 это комплекс белка бетта-лактамазы с амокицилином выделенный из Escherichia coli.
#То есть белок бетта-лактамаза дает бактериям устойчивость к антибиотикам.


In [15]:
# Задание 3
# Загрузим структуру напрямик из базы по ее идентификатору
view = nv.show_pdbid('1LL9') 

In [16]:
from ipywidgets import interact, fixed

representations = [
  'ball+stick',      # шаростержневая модель
  'backbone',        # прямые линии, соединяющие С-альфа атомы
  'cartoon',         # условное отображение вторичной структуры
  'helixorient',     # упрощенное отображение 
  'hyperball',       # сглаженная шаростержневая модель
  'licorice',        # стержневая модель (без шаров)
  'line',            # очень тонкая стержневая модель
  'point',           # атомы в виде плоских точек
  'ribbon',          # отображение остова в виде ленты
  'rocket',          # отображение альфа-спиралей как цилиндров
  'rope',            # отображение остова в виде колбасы
  'spacefill',       # атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса
  'surface',         # поверхность
  'trace',           # сглаженная линия, соединяющая С-альфа атомы
  'tube'             # более сдержанный rope
]


In [17]:
my_examples = {
    'Example 1': {
        'description': '''
Белок из записи 1LL9 в cartoon, 
Белок в виде cartoon, покраска от N к C концу
Боковые радикалы покрашены в светло-серый, показаны линиями
Боковые радикалы заряженных аминокислот показаны в стержневой модели
Лиганды показаны в шаростержневой модели, покрашены по элементам, углерод покрашен в любой цвет, кроме стандартного
''',
        'representations': [
            {
                'type': 'cartoon', #выберем отображение cartoon для объекта который выберем в sale                      
                'params': {
                    'sele': 'protein',             #выбираем  белок 
                    'color': 'residueindex'        # красим от N к C
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'sidechainAttached',              #выбираем боковые радикалы   
                    'color': 'lightGray'                      #красим в светло-серый
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'charged and sidechainAttached',  #выбираем атомы которые И в боковых радикалах И в заряженый аминокислотах 
                    'color': 'brown'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand ',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',        #красим атовы углерода в лиганде в оранжевый    
                    'color': 'orange',
                  
                 }
            },
        ],
    },
    'Example 2': {
        'description': '''
Белок в виде tube, покраска по типу вторичной структуры
Боковые радикалы в стержневой модели, покрашены по гидрофобности
Лиганды показаны линиями, покрашены по элементам
Вода и ионы показаны в виде Ван-дер-Ваальсовых сфер
''',
        'representations': [
            {
                'type': 'tube',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'sstruc'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'hydrophobicity'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
            {
               'type':'spacefill', 
                'params':{
                 'sele':  'water' or 'ion',   
                }
            }
        ],
    },
    'Example 3': {
        'description': '''
Белок в виде cartoon темно-серого цвета
Боковые радикалы в виде линий светло-серого цвета
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'darkgrey'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechainAttached',                     
                    'color': 'lighytgrey'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'sidechainAttached and polar',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                     'sele': 'ligand and _C',                     
                     'color': 'darkblue'  
                 }
            },
        ],
    },
}

In [18]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("1LL9", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 1', 'Example 2', 'Example 3'), va…

NGLWidget()